<p></p>
<br />
<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
		<font color='crimson' size=7>
            Importing the Necessary Libraries
        </font>
	</font>
</div>

In [1]:
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from scipy.stats import gaussian_kde
import plotly.figure_factory as ff
from scipy import stats
from sqlalchemy import create_engine

<p></p>
<br />
<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
		<font color='crimson' size=7>
            Database Connection Setup
        </font>
	</font>
</div>

In [2]:
username = "root"
password = "root"
server = "localhost"
database_url = f"mysql+mysqlconnector://{username}:{password}@{server}:3306/quera_project_phase_1?charset=utf8mb4"
engine = create_engine(database_url)

<p></p>
<br />
<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
		<font color='crimson' size=7>
            1. Relation between Volume and Market Cap
        </font>
		<p></p>
		<hr>
         Querying the sum of the Volume and Market Cap columns, then plotting them using a scatter plot and the Plotly library.
        <br />
	</font>
</div>

In [3]:
query_1 = """
    SELECT date, SUM(volume) AS total_volume, SUM(market_cap) AS total_market_cap
    FROM daily_market
    GROUP BY date
"""

df = pd.read_sql(query_1, engine)

df

date  total_volume  total_market_cap
0    2023-09-10  3.677982e+10      1.025833e+12
1    2023-09-09  2.380896e+10      1.033635e+12
2    2023-09-08  4.289204e+10      1.034169e+12
3    2023-09-07  4.442277e+10      1.043567e+12
4    2023-09-06  5.007018e+10      1.031075e+12
..          ...           ...               ...
359  2022-09-16  1.262461e+11      9.451197e+11
360  2022-09-15  1.636283e+11      9.452360e+11
361  2022-09-14  1.475334e+11      9.850006e+11
362  2022-09-13  1.936690e+11      9.774605e+11
363  2022-09-12  1.783612e+11      1.050679e+12

[364 rows x 3 columns]

In [6]:
fig = px.scatter(
    df,
    x="total_volume",
    y="total_market_cap",
    trendline="ols",
    title="Relation between Volume and Market Cap",
)

fig.update_traces(
    marker=dict(color="#2196F3", size=8, opacity=0.6), line=dict(color="#FE0000")
)

font_family = "Courier New, monospace"
fig.update_xaxes(
    title_text="Volume",
    title_font=dict(family=font_family, size=18),
    tickfont=dict(family=font_family, size=14),
)
fig.update_yaxes(
    title_text="Market Cap",
    title_font=dict(family=font_family, size=18),
    tickfont=dict(family=font_family, size=14),
)

fig.update_layout(title_font=dict(family=font_family,
                  size=22), width=1790, height=600)
fig.show()

results = px.get_trendline_results(fig)

results.px_fit_results.iloc[0].summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                      y   R-squared:                       0.045
Model:                            OLS   Adj. R-squared:                  0.042
Method:                 Least Squares   F-statistic:                     17.00
Date:                Mon, 11 Sep 2023   Prob (F-statistic):           4.64e-05
Time:                        22:22:39   Log-Likelihood:                -9825.0
No. Observations:                 364   AIC:                         1.965e+04
Df Residuals:                     362   BIC:                         1.966e+04
Df Model:                           1                                         
Covariance Type:            nonrobust                                         
==============================================================================
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const       1.082e+12   1.44e+10     75.080      0.000    1.05e+12    1.11e+12
x1            -0.6112      0.148     -4.123      0.000      -0.903      -0.320
==============================================================================
Omnibus:                       33.452   Durbin-Watson:                   1.874
Prob(Omnibus):                  0.000   Jarque-Bera (JB):               25.754
Skew:                          -0.552   Prob(JB):                     2.56e-06
Kurtosis:                       2.308   Cond. No.                     2.09e+11
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
[2] The condition number is large, 2.09e+11. This might indicate that there are
strong multicollinearity or other numerical problems.
"""

<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
         As seen in the chart, there's a decline in Market Cap value based on Volume (assuming we label the daily total of each value as that day's component). However, is this trend consistent across all coins, or are there anomalies? <br>
		 Therefore, we sample and plot the chart for a few coins.
	</font>
</div>

In [7]:
query_coin_id = """
    SELECT id
    FROM coins
"""
ls_coin_id = pd.read_sql(query_coin_id, engine)["id"].tolist()

In [8]:
random_20_id = np.random.choice(ls_coin_id, size=20, replace=False).tolist()
random_20_id

[187,
 136,
 114,
 36,
 25,
 75,
 41,
 23,
 31,
 157,
 7,
 59,
 161,
 10,
 22,
 171,
 193,
 189,
 158,
 55]

In [9]:
query_1_random_coins = """
    SELECT coins.id, coins.name, volume, market_cap
    FROM daily_market
    JOIN coins on daily_market.c_id = coins.id
    WHERE coins.id IN ({})
""".format(
    ",".join(str(id) for id in random_20_id)
)

df_1_random_coins = pd.read_sql(query_1_random_coins, engine)
df_1_random_coins

id                      name       volume    market_cap
0       7                   Cardano  130900000.0  8.739700e+09
1       7                   Cardano   58257400.0  8.894520e+09
2       7                   Cardano  100457000.0  8.925330e+09
3       7                   Cardano  112745000.0  9.042890e+09
4       7                   Cardano  116743000.0  9.040440e+09
...   ...                       ...          ...           ...
6961  193  Kyber Network Crystal v2   79204000.0  3.357940e+08
6962  193  Kyber Network Crystal v2   84964200.0  3.554680e+08
6963  193  Kyber Network Crystal v2   65735300.0  3.443440e+08
6964  193  Kyber Network Crystal v2   91540000.0  3.490040e+08
6965  193  Kyber Network Crystal v2   50963800.0  3.400040e+08

[6966 rows x 4 columns]

In [10]:
subplot_titles = []
for id in random_20_id:
    title = df_1_random_coins[df_1_random_coins["id"] == id]["name"].unique()[
        0]
    subplot_titles.append(title)

fig = make_subplots(rows=4, cols=5, subplot_titles=subplot_titles)

for index, id in enumerate(random_20_id):
    df = df_1_random_coins[df_1_random_coins["id"] == id]

    scatter_fig_lowess = px.scatter(
        df, x="volume", y="market_cap", trendline="lowess")

    scatter_fig_ols = px.scatter(
        df,
        x="volume",
        y="market_cap",
        trendline="ols",
        trendline_options=dict(log_x=True),
    )

    row_num = (index // 5) + 1
    col_num = (index % 5) + 1

    scatter_trace = scatter_fig_lowess["data"][0]
    scatter_trace.showlegend = False
    fig.add_trace(scatter_trace, row=row_num, col=col_num)

    lowess_trace = scatter_fig_lowess["data"][1]
    lowess_trace.line.color = "blue"
    lowess_trace.showlegend = False
    fig.add_trace(lowess_trace, row=row_num, col=col_num)

    ols_trace = scatter_fig_ols["data"][1]
    ols_trace.line.color = "red"
    ols_trace.showlegend = False
    fig.add_trace(ols_trace, row=row_num, col=col_num)

    font_family = "Courier New, monospace"

    fig.update_xaxes(
        title_text="" if row_num != 4 else "Volume",
        title_font=dict(family=font_family, size=18),
        tickfont=dict(family=font_family, size=14),
        showticklabels=True,
        row=row_num,
        col=col_num,
    )

    fig.update_yaxes(
        title_text="Market Cap" if col_num == 1 else "",
        title_font=dict(family=font_family, size=18),
        tickfont=dict(family=font_family, size=14),
        showticklabels=True,
        row=row_num,
        col=col_num,
    )

fig.update_layout(
    title_text="20 Random Coin Data with Lowess and OLS Trendlines",
    width=1790,
    height=1000,
)

fig.show()

<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
         Based on the charts, we observe an approximately logarithmic trend in the data.
	</font>
</div>

In [11]:
df_1_random_coins["log_value_market_cap"] = np.log(
    df_1_random_coins["market_cap"] + 1)
df_1_random_coins["log_value_volume"] = np.log(df_1_random_coins["volume"] + 1)

In [12]:
fig = make_subplots(rows=4, cols=5, subplot_titles=subplot_titles)


for index, id in enumerate(random_20_id):
    df = df_1_random_coins[df_1_random_coins["id"] == id]

    scatter_fig = px.scatter(
        df,
        x="log_value_volume",
        y="log_value_market_cap",
        trendline="ols",
    )

    row_num = (index // 5) + 1
    col_num = (index % 5) + 1

    scatter_trace = scatter_fig["data"][0]
    fig.add_trace(scatter_trace, row=row_num, col=col_num)

    trendline_trace = scatter_fig["data"][1]
    trendline_trace["line"]["color"] = "red"
    fig.add_trace(trendline_trace, row=row_num, col=col_num)

    font_family = "Courier New, monospace"

    fig.update_xaxes(
        title_text="" if row_num != 4 else "Volume",
        title_font=dict(family=font_family, size=18),
        tickfont=dict(family=font_family, size=14),
        showticklabels=True,
        row=row_num,
        col=col_num,
    )

    fig.update_yaxes(
        title_text="Market Cap" if col_num == 1 else "",
        title_font=dict(family=font_family, size=18),
        tickfont=dict(family=font_family, size=14),
        showticklabels=True,
        row=row_num,
        col=col_num,
    )

fig.update_layout(
    title_text="20 Random Coin Data (After Log Transform)",
    title_font=dict(family=font_family, size=22),
    width=1790,
    height=1000,
)

fig.show()

<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
         After applying a logarithmic transformation to the data, we notice a nearly linear trend. From these findings, it's evident that there's a direct correlation between Volume and Market Cap. However, it's essential to note that the specific type of coin plays a crucial role, and this relationship might not hold true for all coins.
	</font>
</div>

<p></p>
<br />
<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
		<font color='crimson' size=7>
            2. Cryptocurrency pairs
        </font>
		<p></p>
		<hr>
         Cryptocurrency pairs with the most synchronized price change days.
        <br />
	</font>
</div>

In [13]:
query_2 = """
    SELECT
        LEAST(first_currency.name, second_currency.name) AS first_currency_name,
        GREATEST(first_currency.name, second_currency.name) AS second_currency_name,
        COUNT(*) AS days_with_synchronized_price_changes
    FROM
        daily_market AS dm1
    JOIN
        daily_market AS dm2 ON dm1.date = dm2.date AND dm1.c_id < dm2.c_id
    JOIN
        coins AS first_currency ON dm1.c_id = first_currency.id
    JOIN
        coins AS second_currency ON dm2.c_id = second_currency.id
    WHERE
        (dm1.close > dm1.open AND dm2.close > dm2.open) OR
        (dm1.close < dm1.open AND dm2.close < dm2.open)
    GROUP BY
        first_currency_name, second_currency_name
    ORDER BY
        days_with_synchronized_price_changes DESC,
        first_currency_name ASC,
        second_currency_name ASC
    LIMIT 30;
"""

results = pd.read_sql_query(query_2, engine)

results

first_currency_name second_currency_name  \
0                 Bitcoin      Wrapped Bitcoin   
1            Decentraland          The Sandbox   
2                Ethereum               Gnosis   
3              Enjin Coin          The Sandbox   
4                Ethereum      Wrapped Bitcoin   
5           Axie Infinity          The Sandbox   
6           Axie Infinity         Decentraland   
7            Decentraland        Oasis Network   
8                 Bitcoin             Ethereum   
9                     BNB          PancakeSwap   
10                   ICON          The Sandbox   
11                   Ankr              Zilliqa   
12                   ICON                 IOST   
13            0x Protocol              VeChain   
14          1inch Network        Oasis Network   
15              Avalanche                 Holo   
16          Axie Infinity        Oasis Network   
17  Basic Attention Token             Ontology   
18                Cardano     Ethereum Classic   
19           Decentraland              VeChain   
20                   ICON            Threshold   
21           Decentraland           Enjin Coin   
22                   Mina        Oasis Network   
23                  Tezos          The Sandbox   
24                   Ankr                 ICON   
25              Avalanche     Ethereum Classic   
26  Basic Attention Token                Tezos   
27                Cardano              Harmony   
28               Ethereum                 Mina   
29          Oasis Network          The Sandbox   

    days_with_synchronized_price_changes  
0                                    350  
1                                    321  
2                                    316  
3                                    314  
4                                    313  
5                                    312  
6                                    311  
7                                    311  
8                                    309  
9                                    309  
10                                   309  
11                                   308  
12                                   307  
13                                   306  
14                                   306  
15                                   306  
16                                   306  
17                                   306  
18                                   306  
19                                   306  
20                                   306  
21                                   305  
22                                   305  
23                                   305  
24                                   304  
25                                   304  
26                                   304  
27                                   304  
28                                   304  
29                                   304

<p></p>
<br />
<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
		<font color='crimson' size=7>
            3. Distribution of Daily Trading Volume of Mineable Cryptocurrencies
        </font>
	</font>
</div>

In [14]:
query_3 = """
    SELECT 
        daily_market.date AS date,
        SUM(daily_market.volume) AS daily_volume
    FROM 
        daily_market
    JOIN 
        coin_tag ON coin_tag.c_id = daily_market.c_id
    JOIN 
        tags ON tags.id = coin_tag.t_id
    JOIN 
        coins ON coins.id = daily_market.c_id
    WHERE 
        tags.name = "Mineable"
    GROUP BY 
        date
    ORDER BY
        daily_market.date
"""

mineable = pd.read_sql(query_3, engine)

mineable

date  daily_volume
0    2022-09-12  5.417655e+10
1    2022-09-13  5.553998e+10
2    2022-09-14  4.199995e+10
3    2022-09-15  4.142530e+10
4    2022-09-16  3.329138e+10
..          ...           ...
359  2023-09-06  1.372842e+10
360  2023-09-07  1.200947e+10
361  2023-09-08  1.166946e+10
362  2023-09-09  6.103326e+09
363  2023-09-10  8.891419e+09

[364 rows x 2 columns]

In [15]:
hist = go.Histogram(x=mineable["daily_volume"], opacity=0.75, name="Histogram")


x_vals = np.linspace(min(mineable["daily_volume"]), max(
    mineable["daily_volume"]), 1000)
kde = gaussian_kde(mineable["daily_volume"])
y_vals = kde(x_vals)

kde_trace = go.Scatter(x=x_vals, y=y_vals, mode="lines",
                       name="KDE", yaxis="y2")

layout_dual_y = go.Layout(
    title="Histogram and KDE for daily_volume with Dual Y-Axis",
    xaxis=dict(title="Value"),
    yaxis=dict(title="Histogram Count"),
    yaxis2=dict(title="KDE Density", overlaying="y", side="right"),
    barmode="overlay",
)

fig_dual_y = go.Figure(data=[hist, kde_trace], layout=layout_dual_y)
fig_dual_y.show()

In [16]:
query_3_daily = """
    SELECT 
        daily_market.volume
    FROM 
        daily_market
    JOIN 
        coin_tag ON coin_tag.c_id = daily_market.c_id
    JOIN 
        tags ON tags.id = coin_tag.t_id
    JOIN 
        coins ON coins.id = daily_market.c_id
    WHERE 
        tags.name = "Mineable"
"""

mineable_daily = pd.read_sql(query_3_daily, engine)

mineable_daily

volume
0     7.899550e+09
1     5.481310e+09
2     1.081740e+10
3     1.108830e+10
4     1.275270e+10
...            ...
8367  3.194760e+07
8368  1.588230e+07
8369  1.324510e+07
8370  2.536560e+07
8371  1.916530e+07

[8372 rows x 1 columns]

In [17]:
hist = go.Histogram(x=mineable_daily["volume"], opacity=0.75, name="Histogram")


x_vals = np.linspace(min(mineable_daily["volume"]), max(
    mineable_daily["volume"]), 1000)
kde = gaussian_kde(mineable_daily["volume"])
y_vals = kde(x_vals)

kde_trace = go.Scatter(x=x_vals, y=y_vals, mode="lines",
                       name="KDE", yaxis="y2")
lower_limit = np.percentile(mineable_daily["volume"], 1)
upper_limit = np.percentile(mineable_daily["volume"], 98)
layout_dual_y = go.Layout(
    title="Histogram and KDE for volume with Dual Y-Axis",
    xaxis=dict(title="Value", range=[lower_limit, upper_limit]),
    yaxis=dict(title="Histogram Count"),
    yaxis2=dict(title="KDE Density", overlaying="y", side="right"),
    barmode="overlay",
)

fig_dual_y = go.Figure(data=[hist, kde_trace], layout=layout_dual_y)
fig_dual_y.show()

<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
         From the charts presented, we can observe that the distribution is right-skewed. This behavior is characteristic of certain distributions, including but not limited to, exponential, gamma, and Weibull distributions.
	</font>
</div>

<p></p>
<br />
<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
		<font color='crimson' size=7>
            4. Correlation Matrix
        </font>
	</font>
</div>

In [18]:
top_coins_query = """
    SELECT coins.id
    FROM daily_market
    JOIN coins ON daily_market.c_id = coins.id
    GROUP BY coins.id
    ORDER BY SUM(daily_market.market_cap) DESC
    LIMIT 16
"""

top_coin_ids = pd.read_sql(top_coins_query, engine)["id"].tolist()

query = """
    SELECT date,
        coins.name,
        (daily_market.close - daily_market.open) AS price_change
    FROM daily_market
    JOIN coins ON coins.id = daily_market.c_id
    WHERE c_id IN ({})
""".format(
    ",".join(str(id) for id in top_coin_ids)
)


price_changes = pd.read_sql(query, engine)

print(price_changes.isnull().sum())
price_changes

date            0
name            0
price_change    0
dtype: int64


date         name  price_change
0     2023-09-10      Bitcoin    -62.984375
1     2023-09-09      Bitcoin     -9.748047
2     2023-09-08      Bitcoin   -339.554688
3     2023-09-07      Bitcoin    491.882812
4     2023-09-06      Bitcoin    -30.695312
...          ...          ...           ...
5819  2022-09-16  Binance USD      0.000686
5820  2022-09-15  Binance USD      0.000353
5821  2022-09-14  Binance USD     -0.000118
5822  2022-09-13  Binance USD      0.000004
5823  2022-09-12  Binance USD      0.000351

[5824 rows x 3 columns]

In [19]:
price_changes_pivot = price_changes.pivot(
    index="date", columns="name", values="price_change"
)
price_changes_pivot

name              BNB  Binance USD      Bitcoin   Cardano       Dai  Dogecoin  \
date                                                                            
2022-09-12  -1.515381     0.000351   600.300781 -0.008205 -0.000515  0.000189   
2022-09-13 -16.072296     0.000004 -2074.773438 -0.032614 -0.000085 -0.003774   
2022-09-14   1.972565    -0.000118    56.535156  0.017464  0.001609  0.001456   
2022-09-15  -8.576172     0.000353  -541.078125 -0.015730 -0.000331 -0.002377   
2022-09-16   3.842316     0.000686    68.578125  0.008422  0.000317  0.001631   
...               ...          ...          ...       ...       ...       ...   
2023-09-06   0.645615     0.000270   -30.695312  0.000046 -0.000073 -0.000384   
2023-09-07   1.747711     0.000625   491.882812  0.000050  0.000038 -0.000034   
2023-09-08  -2.321716    -0.000435  -339.554688 -0.003371  0.000260  0.000063   
2023-09-09  -0.344086    -0.000093    -9.748047 -0.000886  0.000009 -0.000242   
2023-09-10  -1.902542    -0.000322   -62.984375 -0.004443 -0.000746 -0.002078   

name          Ethereum  Litecoin  Polkadot   Polygon     Shiba Inu    Solana  \
date                                                                           
2022-09-12  -48.319580 -0.884144 -0.036541  0.035692 -1.248818e-07  2.456741   
2022-09-13 -133.174561 -2.258518 -0.528012 -0.075627 -6.091086e-07 -3.990791   
2022-09-14   59.896851  1.083828  0.128137  0.018556  9.537871e-08  1.073288   
2022-09-15 -163.389526 -3.799709 -0.276881 -0.040494 -4.960593e-07 -1.046608   
2022-09-16  -39.480591 -0.511215 -0.030106 -0.018335 -1.470435e-07 -0.835735   
...                ...       ...       ...       ...           ...       ...   
2023-09-06   -1.659790 -0.275040  0.012515  0.000425  2.917568e-08 -0.652208   
2023-09-07   15.335449  0.778728  0.017231 -0.003671 -3.669811e-09  0.269419   
2023-09-08  -11.669800 -1.049370 -0.037095 -0.011520 -7.994049e-08 -0.294724   
2023-09-09   -0.888062  0.502911 -0.010053 -0.003239 -2.657589e-08 -0.153934   
2023-09-10  -18.382812 -1.961563 -0.087646 -0.016743 -1.992985e-07 -1.197357   

name            TRON  Tether USDt  USD Coin       XRP  
date                                                   
2022-09-12 -0.000273    -0.000077  0.000051  0.004300  
2022-09-13 -0.002725    -0.000136  0.000092 -0.025772  
2022-09-14  0.000881     0.000103  0.000075  0.009122  
2022-09-15 -0.000354    -0.000135  0.000124 -0.015740  
2022-09-16  0.000034    -0.000021 -0.000051  0.030303  
...              ...          ...       ...       ...  
2023-09-06  0.001438    -0.000116 -0.000021 -0.002188  
2023-09-07  0.000178     0.000276  0.000348  0.001621  
2023-09-08  0.000074     0.000018 -0.000189 -0.000015  
2023-09-09  0.000027     0.000011  0.000098 -0.001004  
2023-09-10 -0.000823    -0.000107 -0.000144 -0.006044  

[364 rows x 16 columns]

In [20]:
correlation_matrix = price_changes_pivot.corr()

z = correlation_matrix.values.tolist()
x = correlation_matrix.columns.tolist()
y = correlation_matrix.index.tolist()

annotation_text = [[f"{val:.3f}" for val in row] for row in z]

fig = ff.create_annotated_heatmap(
    z,
    x=x,
    y=y,
    annotation_text=annotation_text,
    colorscale="RdBu",
    showscale=True,
    reversescale=True,
)

font_family = "Courier New, monospace"

fig.update_xaxes(
    title_text="Cryptocurrency",
    title_font=dict(family=font_family, size=18),
    tickfont=dict(family=font_family, size=14),
)

fig.update_yaxes(
    title_text="Cryptocurrency",
    title_font=dict(family=font_family, size=18),
    tickfont=dict(family=font_family, size=14),
)

fig.update_layout(
    title="Correlation Matrix",
    title_font=dict(family=font_family, size=28),
    width=1790,
    height=600,
)
fig.show()

<p></p>
<br />
<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
		<font color='crimson' size=7>
            5. Advancement during Challenging Times!
        </font>
	</font>
</div>

In [21]:
red_days_subq = """
    SELECT date
    FROM daily_market
    WHERE date BETWEEN '2023-03-01' AND '2023-05-31' 
    GROUP BY date
    HAVING SUM(CASE WHEN close > open THEN 1 ELSE 0 END) * 1.0 / COUNT(*) <= 0.35
"""


crypto_increases_subq = """
    SELECT c_id, COUNT(*) as increase_count
    FROM daily_market
    WHERE date IN (
        {}
    )
    AND close > open
    GROUP BY c_id
""".format(
    red_days_subq
)

top_10_crypto_query = """
    SELECT ci.c_id, ci.increase_count, c.name as coin_name
    FROM (
        {}
    ) AS ci
    JOIN coins c ON ci.c_id = c.id
    ORDER BY ci.increase_count DESC
    LIMIT 10
""".format(
    crypto_increases_subq
)

df = pd.read_sql(top_10_crypto_query, engine)
df

c_id  increase_count     coin_name
0     6              29      USD Coin
1     3              21   Tether USDt
2    12              20           Dai
3    67              20      PAX Gold
4    68              20   Tether Gold
5    19              19  UNUS SED LEO
6    24              17       TrueUSD
7    47              17          USDD
8   103              16      MX TOKEN
9    23              14   Binance USD

In [22]:
coins_ids = df["c_id"].to_list()

top10_volume = """
    SELECT coins.name as coin_name, SUM(daily_market.volume) as total_volume
    FROM coins
    JOIN daily_market ON coins.id = daily_market.c_id
    WHERE coins.id IN ({}) 
    GROUP BY coin_name
""".format(
    ",".join(str(id) for id in coins_ids)
)


top10_volume_df = pd.read_sql(top10_volume, engine)
top10_volume_df

coin_name  total_volume
0   Tether USDt  1.177514e+13
1      USD Coin  1.298579e+12
2           Dai  7.578215e+10
3  UNUS SED LEO  6.363569e+08
4   Binance USD  1.780788e+12
5       TrueUSD  3.001298e+11
6          USDD  1.190913e+10
7      PAX Gold  4.066624e+09
8   Tether Gold  1.278377e+09
9      MX TOKEN  1.101963e+09

In [23]:
top10_volume_df = top10_volume_df.sort_values(
    by="total_volume", ascending=False)

fig = px.bar(
    top10_volume_df,
    x="coin_name",
    y="total_volume",
    text_auto=".2s",
    title="",
)

fig.update_traces(marker_color="crimson")

font_family = "Courier New, monospace"

fig.update_xaxes(
    title_text="Coin Name",
    title_font=dict(family=font_family, size=18),
    tickfont=dict(family=font_family, size=14),
)

fig.update_yaxes(
    title_text="Total Value",
    title_font=dict(family=font_family, size=18),
    tickfont=dict(family=font_family, size=14),
)

fig.update_layout(
    title="Top 10 Coins with Price Increases on Select Red Days",
    title_font=dict(family=font_family, size=28),
    width=1790,
    height=600,
)
fig.show()

<p></p>
<br />
<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
		<font color='crimson' size=7>
            Confidence Interval for the Mean
        </font>
	</font>
</div>

In [24]:
std_query = """
    SELECT volume
    FROM daily_market
"""

std_query_df = pd.read_sql(std_query, engine)
std_pop = std_query_df["volume"].std()
std_pop

3345246315.9699883

In [25]:
np.random.seed(400)
coins_id_query = """
    SELECT coins.id
    FROM coins
"""
coins_id = pd.read_sql(coins_id_query, engine)["id"].tolist()
random_id = np.random.choice(coins_id, size=40, replace=False)

query_avg_volume = """
    SELECT AVG(volume) as average_volume
    FROM daily_market
    WHERE c_id IN ({})
    GROUP BY c_id
""".format(
    ",".join(str(id) for id in random_id)
)

avg_volumes = pd.read_sql(query_avg_volume, engine)
avg_volumes

average_volume
0     1.970278e+08
1     2.442241e+07
2     1.748233e+06
3     9.565499e+07
4     4.892275e+09
5     9.789195e+07
6     2.347306e+08
7     2.169530e+07
8     4.844773e+06
9     8.047474e+07
10    2.884594e+07
11    4.755712e+07
12    1.462576e+08
13    1.300855e+08
14    1.393288e+08
15    1.597320e+06
16    1.863336e+08
17    1.385153e+06
18    3.779487e+07
19    2.779202e+07
20    3.304822e+07
21    1.340111e+07
22    1.261591e+07
23    8.254337e+06
24    1.933972e+07
25    1.179640e+07
26    1.415002e+07
27    2.236704e+07
28    1.047491e+08
29    1.289307e+07
30    2.767509e+07
31    2.251398e+07
32    2.600661e+07
33    8.288517e+06
34    1.376872e+07
35    1.908696e+07
36    1.530993e+07
37    1.310673e+07
38    6.741805e+06
39    1.433874e+07

<p></p>
<br />
<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
		<font color='crimson' size=7>
            Normal Distribution vs. t-Distribution
        </font>
		<p></p>
		<hr>
         For calculating a confidence interval for the mean, we can make use of the normal distribution. Furthermore, given our substantial sample size, the application of the t-distribution, which approaches the normal distribution, is also appropriate (Degrees of Freedom = 39).
        <br />
	</font>
</div>

In [26]:
population_std = avg_volumes["average_volume"].std()

sample_data = avg_volumes["average_volume"]
sample_size = len(avg_volumes)

confidence_level = 0.98

critical_value = stats.norm.ppf((1 + confidence_level) / 2)

margin_of_error = critical_value * (population_std / np.sqrt(sample_size))

sample_mean = np.mean(sample_data)
confidence_interval = (sample_mean - margin_of_error,
                       sample_mean + margin_of_error)

interval_length_normal = confidence_interval[1] - confidence_interval[0]

print("sample mean:", sample_mean)
print("confidence interval:", confidence_interval)
print("confidence interval len:", interval_length_normal)

sample mean: 170429884.91052034
confidence interval: (-112089006.67574325, 452948776.496784)
confidence interval len: 565037783.1725272


In [27]:
ci = np.mean(avg_volumes["average_volume"]) + (
    (np.array(stats.norm.interval(0.98)) * avg_volumes["average_volume"].std())
    / np.sqrt(40)
)
print(
    f"We are 98% sure that the true mean lies between {ci[0]:6f} and {ci[1]:6f}")

We are 98% sure that the true mean lies between -112089006.675743 and 452948776.496784


In [28]:
degrees_of_freedom = sample_size - 1

critical_value = stats.t.ppf((1 + confidence_level) / 2, df=degrees_of_freedom)

sample_mean = np.mean(sample_data)
sample_std = np.std(sample_data, ddof=1)

margin_of_error = critical_value * (sample_std / np.sqrt(sample_size))

confidence_interval = (sample_mean - margin_of_error,
                       sample_mean + margin_of_error)

interval_length_t = confidence_interval[1] - confidence_interval[0]

print("sample mean:", sample_mean)
print("confidence interval:", confidence_interval)
print("confidence interval len:", interval_length_t)

sample mean: 170429884.91052034
confidence interval: (-124171809.82747701, 465031579.6485177)
confidence interval len: 589203389.4759947


In [29]:
interval_length_normal / interval_length_t

0.9589859686228909

<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
         As it's evident, both answers are remarkably close. However, because the t-distribution approximates the normal distribution and may not always align precisely, opting for the normal distribution offers a slightly more accurate approach.
	</font>
</div>

<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
		<font color='crimson' size=7>
            Hypothesis Testing
        </font>
	</font>
</div>

<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
         We posit that X denotes the weekend days, while Y signifies weekdays.
	</font>
</div>

\begin{align*}
H_0 &: \text{Mean of } \textit{X} = \text{Mean of } \textit{Y} \\
H_1 &: \text{Mean of } \textit{X} \neq \text{Mean of } \textit{Y}
\end{align*}


<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
		<font color='aqua' size=5>
            1.What days should I work at Quera?
        </font>
	</font>
</div>

In [30]:
query = """
    SELECT
        c_id,
        date,
        open,
        close
    FROM
        daily_market
"""
df = pd.read_sql_query(query, engine)
df.head()

c_id        date     open    close
0     1  2023-09-10  25895.2  25832.2
1     1  2023-09-09  25905.4  25895.7
2     1  2023-09-08  26245.2  25905.7
3     1  2023-09-07  25748.3  26240.2
4     1  2023-09-06  25783.9  25753.2

In [31]:
df["price_change"] = abs(df["close"] - df["open"])
df["date"] = pd.to_datetime(df["date"])
df["weekday"] = df["date"].dt.day_name()
df.head()

c_id       date     open    close  price_change    weekday
0     1 2023-09-10  25895.2  25832.2          63.0     Sunday
1     1 2023-09-09  25905.4  25895.7           9.7   Saturday
2     1 2023-09-08  26245.2  25905.7         339.5     Friday
3     1 2023-09-07  25748.3  26240.2         491.9   Thursday
4     1 2023-09-06  25783.9  25753.2          30.7  Wednesday

In [32]:
weekend_df = df[df["date"].dt.dayofweek.isin([3, 4, 5])]
weekday_df = df[df["date"].dt.dayofweek.isin([6, 0, 1])]
print("Weekend DataFrame:")
print(weekend_df)

print("Weekday DataFrame:")
print(weekday_df)

Weekend DataFrame:
       c_id       date          open         close  price_change   weekday
1         1 2023-09-09  25905.400000  25895.700000      9.700000  Saturday
2         1 2023-09-08  26245.200000  25905.700000    339.500000    Friday
3         1 2023-09-07  25748.300000  26240.200000    491.900000  Thursday
8         1 2023-09-02  25800.900000  25868.800000     67.900000  Saturday
9         1 2023-09-01  25934.000000  25800.700000    133.300000    Friday
...     ...        ...           ...           ...           ...       ...
70432   200 2022-09-23      0.004958      0.005010      0.000052    Friday
70433   200 2022-09-22      0.004862      0.004957      0.000096  Thursday
70438   200 2022-09-17      0.005312      0.005443      0.000131  Saturday
70439   200 2022-09-16      0.005426      0.005309      0.000117    Friday
70440   200 2022-09-15      0.005615      0.005414      0.000200  Thursday

[30195 rows x 6 columns]
Weekday DataFrame:
       c_id       date          open

In [33]:
hist = go.Histogram(x=weekend_df["price_change"], opacity=0.75, name="Histogram")

x_vals = np.linspace(
    min(weekend_df["price_change"]), max(weekend_df["price_change"]), 4000
)
kde = gaussian_kde(weekend_df["price_change"])
y_vals = kde(x_vals)

kde_trace = go.Scatter(x=x_vals, y=y_vals, mode="lines", name="KDE", yaxis="y2")

lower_limit = np.percentile(weekend_df["price_change"], 1)
upper_limit = np.percentile(weekend_df["price_change"], 99)

layout_dual_y = go.Layout(
    title="Histogram and KDE for volume with Dual Y-Axis for weekend days",
    xaxis=dict(title="Value", range=[lower_limit, upper_limit]),
    yaxis=dict(title="Histogram Count"),
    yaxis2=dict(title="KDE Density", overlaying="y", side="right"),
    barmode="overlay",
)

fig_dual_y = go.Figure(data=[hist, kde_trace], layout=layout_dual_y)
fig_dual_y.show()

In [34]:
hist = go.Histogram(x=weekday_df["price_change"], opacity=0.75, name="Histogram")


x_vals = np.linspace(
    min(weekday_df["price_change"]), max(weekday_df["price_change"]), 4000
)
kde = gaussian_kde(weekday_df["price_change"])
y_vals = kde(x_vals)

kde_trace = go.Scatter(x=x_vals, y=y_vals, mode="lines", name="KDE", yaxis="y2")

lower_limit = np.percentile(weekday_df["price_change"], 1)
upper_limit = np.percentile(weekday_df["price_change"], 99)

layout_dual_y = go.Layout(
    title="Histogram and KDE for volume with Dual Y-Axis for weekdays",
    xaxis=dict(title="Value", range=[lower_limit, upper_limit]),
    yaxis=dict(title="Histogram Count"),
    yaxis2=dict(title="KDE Density", overlaying="y", side="right"),
    barmode="overlay",
)

fig_dual_y = go.Figure(data=[hist, kde_trace], layout=layout_dual_y)
fig_dual_y.show()

In [35]:
var_weekend = np.var(weekend_df["price_change"])
var_weekday = np.var(weekday_df["price_change"])

print(var_weekend)
var_weekday

3389.3785223330297


3563.7323045737567

<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
         From the graphs, it's evident that the distributions aren't normal, making the t-test inapplicable. Instead, we'll employ the Mann-Whitney test, a non-parametric method that doesn't necessitate conditions like normality or equality of variance.
	</font>
</div>

<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
         We posit that X denotes the weekend days, while Y signifies weekdays.
	</font>
</div>

\begin{align*}
H_0 &: \text{The distribution of } \textit{X} \text{ is the same as the distribution of } \textit{Y} \\
H_1 &: \text{The distribution of } \textit{X} \text{ is different from the distribution of } \textit{Y} \\
& \\
& \text{In other words,} \\
& \\
H_0 &: \text{Median (or Mean) of } \textit{X} = \text{Median (or Mean) of } \textit{Y} \\
H_1 &: \text{Median (or Mean) of } \textit{X} = \text{Median (or Mean) of } \textit{Y}
\end{align*}



<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
                The Mann-Whitney U test, is chosen because the data does not follow a normal distribution. This non-parametric test compares the distributions of two independent samples without making strict assumptions about the specific distribution from which the data originated.<br>
                We reference the medians when interpreting the results of the Mann-Whitney U test because the median, being a measure of central tendency, accurately reflects the center of a distribution. It remains unaffected by outliers, making it a more reliable measure especially for non-normally distributed data. Though the test doesn't directly pit medians (or means) against each other, a significant outcome indicates a difference in the central tendencies of the two groups.
        </font>
</div>

<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
		<font color='aqua' size=5>
            Performing Man-Whitney test:
        </font>
	</font>
</div>

In [36]:
statistic, p_value = stats.mannwhitneyu(
    weekend_df["price_change"], weekday_df["price_change"]
)
p_value

0.04668199064879598

<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
                As evident, the p-value under consideration lacks the decisiveness to reject the null hypothesis outright. Its determination hinges on the threshold we establish for our testing.
        </font>
</div>

<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
                For instance, when we set the alpha value at 0.01, we lack sufficient evidence to reject the null hypothesis, resulting in its acceptance. In other words, for alpha values less than the p-value, the null hypothesis remains unchallenged (This implies that there is no statistically meaningful difference on the mentioned days, even though various factors such as coin flips and others could be considered. The test results do not reveal any significant distinctions). Conversely, with an alpha of 0.05, we reject the null hypothesis in favor of the alternative hypothesis.
        </font>
</div>

<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
                For instance, when dealing with alphas lower than the obtained P-value, the following steps should be taken:<br>
                The null hypothesis is rejected in favor of the alternative hypothesis, indicating a statistically significant difference between the means. Subsequently, our focus shifts to identifying the specific days with higher average values. To achieve this, we perform a comparison of the means from two separate data frames:
    </font>
</div>

In [37]:
print("weekday mean:", np.mean(weekday_df["price_change"]))
print("weekend mean:", np.mean(weekend_df["price_change"]))

weekday mean: 5.414232530538837
weekend mean: 5.141627663082282


<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
                Given the values above, working in Quera during the weekends seems reasonable due to the lower average. This way, we don't miss out on the more volatile days. However, it's important to note that alphas below the P-value threshold are quite strict in their judgment about our issue!
    </font>
</div>

<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
		<font color='aqua' size=5>
            2. Which Side is better?
        </font>
	</font>
</div>

In [38]:
btc_eth_usdt_query = """SELECT
                            daily_market.c_id, 
                            daily_market.date, 
                            daily_market.volume 
                        FROM
                            daily_market
                        JOIN 
                            coins ON coins.id = daily_market.c_id
                        WHERE 
                            coins.name IN ('Bitcoin', 'Ethereum', 'Thether USDt')"""


others_query = """SELECT
                    daily_market.c_id,
                    daily_market.date,
                    daily_market.volume 
                  FROM 
                    daily_market
                  JOIN 
                    coins ON coins.id = daily_market.c_id
                  WHERE 
                    coins.name NOT IN ('Bitcoin', 'Ethereum', 'Thether USDt')"""

<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
		<font color='aqua' size=5>
            Reading Queries
        </font>
	</font>
</div>

In [39]:
btc_eth_usdt_results = pd.read_sql_query(btc_eth_usdt_query, engine)
others_results = pd.read_sql_query(others_query, engine)

<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
		<font color='aqua' size=5>
            Printing data
        </font>
	</font>
</div>

In [40]:
print(btc_eth_usdt_results)
print(others_results)

     c_id        date        volume
0       1  2023-09-10  7.899550e+09
1       1  2023-09-09  5.481310e+09
2       1  2023-09-08  1.081740e+10
3       1  2023-09-07  1.108830e+10
4       1  2023-09-06  1.275270e+10
..    ...         ...           ...
723     2  2022-09-16  1.676480e+10
724     2  2022-09-15  2.694630e+10
725     2  2022-09-14  1.789720e+10
726     2  2022-09-13  2.306680e+10
727     2  2022-09-12  1.768840e+10

[728 rows x 3 columns]
       c_id        date       volume
0       154  2023-09-10    6947710.0
1       154  2023-09-09    5708790.0
2       154  2023-09-08   10299500.0
3       154  2023-09-07    9355730.0
4       154  2023-09-06    9129790.0
...     ...         ...          ...
69711   105  2022-09-16   41016600.0
69712   105  2022-09-15   56575700.0
69713   105  2022-09-14   59656300.0
69714   105  2022-09-13  117672000.0
69715   105  2022-09-12  161057000.0

[69716 rows x 3 columns]


<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
		<font color='aqua' size=5>
            Now, we will examine the normality of the distributions:
        </font>
	</font>
</div>

In [41]:
btc_eth_usdt = btc_eth_usdt_results["volume"]


hist = go.Histogram(x=btc_eth_usdt_results["volume"], opacity=0.75, name="Histogram")


x_vals = np.linspace(
    min(btc_eth_usdt_results["volume"]), max(btc_eth_usdt_results["volume"]), 4000
)
kde = gaussian_kde(btc_eth_usdt_results["volume"])
y_vals = kde(x_vals)

kde_trace = go.Scatter(x=x_vals, y=y_vals, mode="lines", name="KDE", yaxis="y2")

layout_dual_y = go.Layout(
    title="Histogram and KDE for daily volume with Dual Y-Axis for 3 Specific Coins",
    xaxis=dict(title="Value"),
    yaxis=dict(title="Histogram Count"),
    yaxis2=dict(title="KDE Density", overlaying="y", side="right"),
    barmode="overlay",
)

fig_dual_y = go.Figure(data=[hist, kde_trace], layout=layout_dual_y)
fig_dual_y.show()

In [42]:
others = others_results["volume"]

hist = go.Histogram(x=others_results["volume"], opacity=0.75, name="Histogram")


x_vals = np.linspace(min(others_results["volume"]), max(others_results["volume"]), 4000)
kde = gaussian_kde(others_results["volume"])
y_vals = kde(x_vals)

kde_trace = go.Scatter(x=x_vals, y=y_vals, mode="lines", name="KDE", yaxis="y2")

lower_limit = np.percentile(others_results["volume"], 1)
upper_limit = np.percentile(others_results["volume"], 99)

layout_dual_y = go.Layout(
    title="Histogram and KDE for volume with Dual Y-Axis for other Coins",
    xaxis=dict(title="Value", range=[lower_limit, upper_limit]),
    yaxis=dict(title="Histogram Count"),
    yaxis2=dict(title="KDE Density", overlaying="y", side="right"),
    barmode="overlay",
)

fig_dual_y = go.Figure(data=[hist, kde_trace], layout=layout_dual_y)
fig_dual_y.show()

<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
		<font color='aqua' size=5>
            Checking the equality of variances:
        </font>
	</font>
</div>

In [43]:
var_btc_eth_usdt = np.var(btc_eth_usdt)
var_others = np.var(others)

print(var_btc_eth_usdt)
var_others

1.5069958955169717e+20


7.353600609583633e+18

<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
         From the graphs, it's evident that the distributions aren't normal, making the t-test inapplicable. Instead, we'll employ the Mann-Whitney test, a non-parametric method that doesn't necessitate conditions like normality or equality of variance.
	</font>
</div>

<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
         We posit that X denotes the three designated coins volume, while Y signifies all other coins volume.
	</font>
</div>

\begin{align*}
H_0 &: \text{The distribution of } \textit{X} \text{ is the same as the distribution of } \textit{Y} \\
H_1 &: \text{The distribution of } \textit{X} \text{ is different from the distribution of } \textit{Y} \\
& \\
& \text{In other words,} \\
& \\
H_0 &: \text{Median (or Mean) of } \textit{X} = \text{Median (or Mean) of } \textit{Y} \\
H_1 &: \text{Median (or Mean) of } \textit{X} = \text{Median (or Mean) of } \textit{Y}
\end{align*}



<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
                The Mann-Whitney U test, is chosen because the data does not follow a normal distribution. This non-parametric test compares the distributions of two independent samples without making strict assumptions about the specific distribution from which the data originated.<br>
                We reference the medians when interpreting the results of the Mann-Whitney U test because the median, being a measure of central tendency, accurately reflects the center of a distribution. It remains unaffected by outliers, making it a more reliable measure especially for non-normally distributed data. Though the test doesn't directly pit medians (or means) against each other, a significant outcome indicates a difference in the central tendencies of the two groups.
        </font>
</div>

<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
		<font color='aqua' size=5>
            Performing Man-Whitney test:
        </font>
	</font>
</div>

In [44]:
statistic, p_value = stats.mannwhitneyu(btc_eth_usdt, others)
p_value

0.0

<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
                As evident, the null hypothesis is dismissed due to a p-value of zero, indicating a discrepancy between the means of the two datasets. But which dataset holds the edge? To discern the direction of this variation, we'll compute the means of the datasets:
        </font>
</div>

In [45]:
mean_btc_eth_usdt = np.mean(btc_eth_usdt)
mean_others = np.mean(others)

print("mean of 3 coins:", mean_btc_eth_usdt)
print("mean of other coisn:", mean_others)

mean of 3 coins: 15463874491.758242
mean of other coisn: 287965939.4335705


<div id="sec_intro_to_intro" style="direction:ltl;line-height:300%;">
	<font face="XB Zar" size=5>
                Based on the obtained averages, we can conclude that the null hypothesis is rejected in favor of the alternative. This implies that the average daily trading volumes of 'Bitcoin', 'Ethereum', and 'Tether USDt' are significantly higher than those of other cryptocurrencies
        </font>
</div>